In [22]:
from pymongo import MongoClient
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
import colorlover as cl

In [35]:
uri = "mongodb://127.0.0.1"
mongo = MongoClient(uri)

DC = {"lat": 38.93, "lon": -76.98}
LA = { "lat": 34.0522, "lon": -118.2437}

CENTER = LA

gradient = cl.scales['8']['div']['RdYlBu']

In [51]:
def get_path(route):
    lat, lng = [], []
    try:
        for point in route["data"]["data"]["directions"]["points"]:
            lat.append(point["lat"])
            lng.append(point["lng"])
        return lat, lng
    except:
        return None

cache = {}
def get_address(hash_):
    addr = cache.get(hash_)
    if addr is None:
        addr = db.dc.find_one({"HASH": hash_})
    if addr is None:
        addr = db.la.find_one({"HASH": hash_})
    if addr:
        cache[hash_] = addr
    return addr

def remap(x, in_min, in_max, out_min, out_max):
  return (x - in_min) * (out_max - out_min) / (in_max - in_min) + out_min

db = mongo.main
fig = go.Figure()
fig.add_trace(go.Scattergeo(locationmode = 'USA-states'))

for ride in db.routes.find():
    pickup, destination = ride["pickup"], ride["destination"]
    pickup_addr, destination_addr = get_address(pickup), get_address(destination)
    if ride.get("prices") is None:
        continue
    prices = {x[0]: x[1] for x in ride["prices"]}
    if prices.get("UberX") is None:
        continue
    dollars_per_mile = float(prices["UberX"])/(ride["distance"]/1609.344)
    route = db.directions.find_one({"pickup": pickup, "destination": destination})
    if route is None:
        continue
    path = get_path(route)
    if path is None:
        continue
    fig.add_trace(go.Scattergeo(
        name = "{} - {}".format(pickup_addr["STREET"], destination_addr["STREET"]),
        lat = path[0],
        lon = path[1],
        mode = "lines",
        hoverlabel = dict(namelength = -1),
        line = dict(width = 0.5, color = gradient[int(remap(dollars_per_mile, 2, 6, 0, len(gradient)))]),
        text = "${:.2f}/mi, {:.2f}mi".format(dollars_per_mile, ride["distance"]/1609.344),
        opacity = 0.3,
        )
    )
    
fig.update_layout(
    autosize = False,
    showlegend = False,
    width = 1000,
    height = 800,
    geo = go.layout.Geo(
        center = CENTER,
        projection = { "scale": 600 }
    )
)
fig.show()